In [1]:
import MySQLdb

import pandas as pd

import re
import json

In [2]:
location = "127.0.0.1"

user = "root"

password = ""

database_name = "bigcookingdata"

db = None

cursor = None

def connect():
    global cursor
    global db
    db = MySQLdb.connect(location,user,password,database_name )
    cursor = db.cursor()
def disconnect():
    db.close()

def get_version():
    cursor.execute( "SELECT VERSION()" )
    return cursor.fetchone()[0]

In [3]:
# Create Databases
def createDB():
    connect()
    sql_create_db = """
        DROP TABLE IF EXISTS assess;
        DROP TABLE IF EXISTS client;
        DROP TABLE IF EXISTS contain_recipe_ingredient;
        DROP TABLE IF EXISTS have_preferences_ingredient;
        DROP TABLE IF EXISTS ingredient;
        DROP TABLE IF EXISTS recipe;
        DROP TABLE IF EXISTS record;


       CREATE TABLE assess (
        id_recipe int(11) NOT NULL,
        id_client int(11) NOT NULL,
        rating tinyint(4) DEFAULT NULL,
        date_assess CHAR(10) DEFAULT NULL,
        commentary varchar(280) DEFAULT NULL,
        PRIMARY KEY (id_recipe,id_client),
        KEY id_client (id_client)
        ) ENGINE=MyISAM DEFAULT CHARSET=latin1
        ;

        CREATE TABLE client (
        id_client int(11) NOT NULL,
        firstname varchar(25) DEFAULT NULL,
        lastname varchar(25) DEFAULT NULL,
        civility char(2) DEFAULT NULL,
        pseudo varchar(25) DEFAULT NULL,
        mail varchar(40) DEFAULT NULL,
        password varchar(30) DEFAULT NULL,
        PRIMARY KEY (id_client)
        ) ENGINE=MyISAM DEFAULT CHARSET=latin1;

        CREATE TABLE have_preferences_ingredient (
        id_client int(11) NOT NULL,
        id_ingredient int(11) NOT NULL,
        PRIMARY KEY (id_client,id_ingredient),
        KEY id_ingredient (id_ingredient)
        ) ENGINE=MyISAM DEFAULT CHARSET=latin1;

        CREATE TABLE ingredient (
          id_ingredient int(11) NOT NULL,
          name varchar(40) DEFAULT NULL,
          url_pic text DEFAULT NULL,
          is_active int(11) DEFAULT NULL,
          PRIMARY KEY (id_ingredient)
        ) ENGINE=MyISAM DEFAULT CHARSET=latin1;


        CREATE TABLE recipe (
          id_recipe int(11) NOT NULL,
          name varchar(50) DEFAULT NULL,
          categories text,
          url_pic text,
          clusterNumber varchar(20) NOT NULL,
          directions text,
          prep_time varchar(20) DEFAULT NULL,
          cook_time varchar(20) DEFAULT NULL,
          break_time varchar(20) DEFAULT NULL,
          difficulty varchar(15) DEFAULT NULL,
          close_to TEXT DEFAULT NULL,
          budget varchar(15) DEFAULT NULL,
          serving varchar(6) DEFAULT NULL,
          coordonnees text DEFAULT NULL,
          id_author int(11) DEFAULT NULL,
          PRIMARY KEY (id_recipe)
        ) ENGINE=MyISAM DEFAULT CHARSET=latin1;
        
        CREATE TABLE contain_recipe_ingredient (
          id_recipe int(11) NOT NULL,
          id_ingredient int(11) NOT NULL,
          quantity varchar(20) DEFAULT NULL,
          unity varchar(20) DEFAULT NULL,
          PRIMARY KEY (id_recipe,id_ingredient),
          KEY id_ingredient (id_ingredient)
        )ENGINE=MyISAM DEFAULT CHARSET=latin1;



        CREATE TABLE record (
          id_recipe int(11) NOT NULL,
          id_client int(11) NOT NULL,
          PRIMARY KEY (id_recipe,id_client),
          KEY id_client (id_client)
        ) ENGINE=MyISAM DEFAULT CHARSET=latin1;
    
    """
#     global sql_assess,sql_contain_recipe_ingredient,sql_have_preferences_ingredient,sql_ingredient
#     global sql_recipe,sql_client,sql_record,table_recipe,table_user
    sql_assess = "drop table assess;"
    sql_contain_recipe_ingredient = "drop table contain_recipe_ingredient;"
    sql_have_preferences_ingredient = "drop table have_preferences_ingredient;"
    sql_ingredient = "drop table ingredient;"
    sql_recipe = "drop table recipe;"
    sql_client = "drop table client;"
    sql_record = "drop table record;"
    table_recipe = 'l_recipe_ingredient'
    table_user = 'user'
    _SQL = """SHOW TABLES"""
    try:
#         cursor.execute( _SQL )
        cursor.execute( sql_create_db )
        results = cursor.fetchall()
        print( 'All existing tables:', results )  # Returned as a list of tuples
    except (MySQLdb.Error, MySQLdb.Warning) as e:
        print('error')
        print(e)
    results_list = [item[0] for item in results]  # Conversion to list of str
    if(table_recipe and table_user in results_list):
        print(table_recipe, table_record, table_user, "was found")
        try:
            # Execute the SQL command
            cursor.execute(sql_recipe)
            cursor.execute(sql_ingredient)
            cursor.execute(sql_ingredient)
            cursor.execute(sql_client)
            cursor.execute(sql_assess)
            cursor.execute(sql_contain_recipe_ingredient)
            cursor.execute(sql_have_preferences_ingredient)
            cursor.execute(sql_record)
            cursor.execute(sql_create_db)
            # Commit your changes in the database
            db.commit()
        except (MySQLdb.Error, MySQLdb.Warning) as e:
                db.rollback()
                print(e)
    else:
        print(table_recipe, table_user, "was found")
        try:
#             cursor.execute(sql_drop)
            cursor.execute( sql_create_db )
        except:
            db.rollback()
            disconnect()

            

In [4]:
createDB()

All existing tables: ()
l_recipe_ingredient user was found


In [4]:
def persisetDB(recipes):
    global sql_assess,sql_contain_recipe_have_preferences_ingredient,sql_ingredient,sql_recipe
    global sql_client,sql_record,  liste_ingre_totale_pd, categories, categorie_str, liste_ingre,dict_ingre
    global ing_id_unique, ing_quantity,list_utensil_total_pd,title_recipe,ingre, id_fetch,id_fetch_rec
    
    listDic_Ingre = []
    dict_ingre = {}
    connect()
    ################# Création table ingredients sans doublons #####################
    for values in recipes:
        ingredients = values['ingredients']
        categories =  values['category']
        difficulty =  values['difficulty']
        budget =  values['budget']
        directions =  "NO VALUES"
        if ingredients is None:
            pass
            print( "0 ingrédients" )
        else:
            for ing in ingredients:
                liste_ingre = []
                dict_Ingre = {}
                ing_id_unique = 0
                ing_name = re.escape( str( ing['nom_ingre']))
                ing_img_url = re.escape( str( ing['image_ingre']))
                dict_Ingre[ing_name] = ing_img_url
                listDic_Ingre.append(dict_Ingre)
               
                                        
#     print( "LEN LIST INGREDIENT :",listDic_Ingre)
    newListIngre = [i for n, i in enumerate(listDic_Ingre) if i not in listDic_Ingre[n + 1:]]
#     print( "LEN LIST INGREDIENT :",newListIngre)

    #insert ingredients in base
    counter = 0
    for key,ingredient in enumerate(newListIngre):
        key += 1
        for ingre, url_pic in ingredient.items():
            ingre = ingre.replace('\u0301', ' ')
            ingre = ingre.replace('\u00ae\ufe0f', ' ')
            sql_ingredient = """ insert into ingredient
            (name,id_ingredient,url_pic) values("%s","%s","%s");""" % (ingre, key,url_pic)
        print( "INGREDIENT :", sql_ingredient )

        try:
            # Execute the SQL command ingredient
            cursor.execute( sql_ingredient )
            # Commit your changes in the database
            db.commit()
        except:
            # Rollback in case there is any error
            db.rollback()
            
    
    # insert recette
    compteur = 0
   
    for values in recipes:
        name=  values.get('nom')
        name = name.replace("\"", "\\'")
        name = name.replace('\u0301', ' ')
        name = name.replace('\u00ae\ufe0f', ' ')
        prep_time =   values.get( 'time_prepa' )
        cook_time =   values.get( 'time_cuisson' )
        break_time =  values.get( 'time_repo' )
        rating = values.get( 'global_rating' )
        difficulty =  values.get( 'difficulty' )
        budget =  values.get( 'budget' )
        categories =  values.get( 'category' )
        categories = ';'.join(categories)
        categories = categories.replace(",", " ")
        
        title_recipe =  values.get( 'title' )
        # directionx =  values.get( 'etape' )
        # directions = '||'.join(directionx)
        directions = ""
        url_pic =  values.get('img_url')

        clusterNumber = values.get('cluster')
        coordonnees = values.get('coordonnees')
        serving = 1

         # Affichage numerous recipe et compteur
        compteur = compteur + 1
#         print( "--- NUMEROUS RECIPE :", compteur, ":", name, "---" )

        # Condition if None everywhere
        if not name and not budget and not difficulty and not categories and not rating:
            name = 0
            prep_time =  0
            cook_time = 0
            break_time =0
            rating = 0
            difficulty = 0
            budget = 0
            categories = 0
            title_recipe =0
            coordonnees = 0
            clusterNumber = 0.0

            sql_recipe = """insert into recipe (id_recipe,name,categories,url_pic,clusterNumber,directions,prep_time,cook_time,
            break_time,difficulty,budget,serving,coordonnees)\
                                        values ("%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s");"""  % (
                    compteur,name, categories,url_pic, clusterNumber, directions, prep_time, cook_time, break_time,
                    difficulty,budget,serving,coordonnees)
            
      
        # Condition for Categories
        if categories is None:
            categories = 'Vide'
            print( "0 categorie" )
        else:
            pass
        
        if budget is None:
                budget = 0
                sql_recipe = """insert into recipe (id_recipe,name,categories,url_pic,clusterNumber,directions,prep_time,cook_time,
                                break_time,difficulty,budget,serving,coordonnees)\
                                values ("%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s");"""  % (
                    compteur,name, categories, url_pic, clusterNumber, directions, prep_time, cook_time, break_time,
                    difficulty,budget,serving,coordonnees)
                
        elif rating is None:
                rating = 0
                sql_recipe = """insert into recipe (id_recipe,name,categories,url_pic,clusterNumber,directions,prep_time,cook_time,
                                break_time,difficulty,budget,serving,coordonnees)\
                                 values ("%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s");""" % (
                    compteur,name, categories, url_pic, clusterNumber, directions, prep_time, cook_time, break_time,
                    difficulty,budget,serving,coordonnees)
                
        else:
             sql_recipe = """insert into recipe (id_recipe,name,categories,url_pic,clusterNumber,directions,prep_time,cook_time,
                                break_time,difficulty,budget,serving,coordonnees)\
                                values ("%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s","%s");"""  % (
                   compteur, name, categories, url_pic, clusterNumber, directions, prep_time, cook_time, break_time,
                    difficulty,budget,serving,coordonnees)
                
                
        print( "RECIPE ::", sql_recipe )
        
        # Injection des recipes en base
        try:
            # Execute the SQL command recipe
            cursor.execute(sql_recipe)
            # Commit your changes in the database
            db.commit()
        except (MySQLdb.Error, MySQLdb.Warning) as e:
                db.rollback()
                print(e)
                
        # liaison recette  recette ingredients
    compteur = 0
    for values in recipes:
        ingredients =  values['ingredients']
        title_recipe =  values['nom']
        title_recipe = title_recipe.replace("\"", "\\'")
        title_recipe = title_recipe.replace('\u0301', ' ')
        title_recipe = title_recipe.replace('\u00ae\ufe0f', ' ')
        title_recipe = str(title_recipe)
        if ingredients is None:
            pass
            print( "0 ingrédients" )
        else:
            for ing in ingredients:
                ing_quantity = ing['quantity']
                ing_unity = ing['unity']
                if(ing_quantity != 'empty'):
                    # ing_unity = ''.join(ing_quantity)
                    ing_unity = ing_unity.replace('\u00a0', '')
                ing_name = re.escape( str( ing['nom_ingre']))
                ing_name = ing_name.replace('\u0301', ' ')
                ing_name = ing_name.replace('\u00ae\ufe0f', ' ')
                ing_img_url = re.escape( str( ing['image_ingre']))
                sql_get_id_ingredient = """select id_ingredient from ingredient 
                where name= "%s";""" % (ing_name)
                print( "SQL GET ID INGRE :::::::::", sql_get_id_ingredient )
                sql_get_id_recipe = """select id_recipe from recipe where name= "%s";""" % (title_recipe)
                print( "GET ID RECIPE :", sql_get_id_recipe )
                id_fetch_rec = 0
                id_fetch = 0

                try:
                    cursor.execute(
                        """select id_recipe from recipe where name= "%s";""" % (title_recipe) )
                    id_rec = cursor.fetchall()
                    for id_rec_att in id_rec:
                        id_fetch_rec = id_rec_att[0]
                        print( "CLE PRIMAIRE RECIPE :", id_fetch_rec )
                        print("TITRE RECIPE :::::", title_recipe)
                        print("++++++++++++++++++++++++")
                except (MySQLdb.Error, MySQLdb.Warning) as e:
                        db.rollback()
                        print( "Error get ID Recipe" )
                        print(e)
                try:
                    cursor.execute(
                        """select id_ingredient from ingredient where name= "%s";""" % (ing_name) )
                    id_ingre = cursor.fetchall()
                    for id_att in id_ingre:
                        id_fetch = id_att[0]
                        print( "CLE PRIMAIRE ING = ", id_fetch )
                        print( "Title Ingredient = ", ing_name )
                except (MySQLdb.Error, MySQLdb.Warning) as e:
                    print( "Error get ID Ingredient" )
                    db.rollback()
                    print(e)
                if ing_quantity is None:
                    sql_l_recipe_ingredient = """ insert into contain_recipe_ingredient (id_recipe,id_ingredient,quantity,unity) values("%s","%s","%s","%s");""" % (
                    id_fetch_rec, id_fetch, None,None)
                    print( "LIAISON INGREDIENT : None Quantity", sql_l_recipe_ingredient )
                elif ing_unity is None :
                    sql_l_recipe_ingredient = """ insert into contain_recipe_ingredient (id_recipe,id_ingredient,quantity,unity)  values("%s","%s","%s","%s");""" % (
                    id_fetch_rec, id_fetch, ing_quantity, None)
                    print( "LIAISON INGREDIENT :", sql_l_recipe_ingredient )
                else:
                    sql_l_recipe_ingredient = """ insert into contain_recipe_ingredient (id_recipe,id_ingredient,quantity,unity)  values("%s","%s","%s","%s");""" % (
                    id_fetch_rec, id_fetch, ing_quantity, ing_unity)
                    print( "LIAISON INGREDIENT :", sql_l_recipe_ingredient )   
                try:
                    # Execute the SQL command liaison
                    cursor.execute( sql_l_recipe_ingredient )
                        # Commit your changes in the database
                    db.commit()
                except:
                    # Rollback in case there is any error
                    db.rollback()




In [5]:
def readJson(file):
    json_file = open(file, encoding='utf-8')
    data = json_file.read()
    recipes = json.loads(data)
    json_file.close()
    return recipes

In [6]:

recette1 = readJson('data/_second.json')
persisetDB(recette1)
recette2 = readJson('data/_third.json')
persisetDB(recette2)

INGREDIENT :  insert into ingredient
            (name,id_ingredient,url_pic) values("nappage","1","https://assets\.afcdn\.com/recipe/20100101/ingredient_default_w96h96c1\.jpg");
INGREDIENT :  insert into ingredient
            (name,id_ingredient,url_pic) values("farine\ sans\ gluten","2","https://assets\.afcdn\.com/recipe/20100101/ingredient_default_w96h96c1\.jpg");
INGREDIENT :  insert into ingredient
            (name,id_ingredient,url_pic) values("lait\ de\ riz","3","https://assets\.afcdn\.com/recipe/20210308/118438_w96h96c1cx315cy276cxb631cyb553\.jpg");
INGREDIENT :  insert into ingredient
            (name,id_ingredient,url_pic) values("tofu\ soyeux","4","https://assets\.afcdn\.com/recipe/20171110/74687_w96h96c1cx2651cy2442cxb5302cyb4884\.jpg");
INGREDIENT :  insert into ingredient
            (name,id_ingredient,url_pic) values("macreuse","5","https://assets\.afcdn\.com/recipe/20100101/ingredient_default_w96h96c1\.jpg");
INGREDIENT :  insert into ingredient
            (name,id

In [8]:
img = 'https://assets.afcdn.com/recipe/20190220/88075_w1200h911.jpg'
# img = 'https://assets.afcdn.com/recipe/20100101/recipe_default_img_placeholder_w96h96c1.jpg'
img = img.split("/")
img5 = img[5].split("_")
if len(img5) >=4:
    img_url = img[0] + "//" + img[2] + "/" +img[3] + "/"+ img[4] + "/" + img5[0] + "_" + img5[1] + "_" + img5[2] + "_" + img5[3] + "_" + "w1000h1000.jpg"
else:
    img_url = img[0] + "//" + img[2] + "/" +img[3] + "/"+ img[4] + "/" + img5[0] + "_" + "_" + "w1000h1000.jpg"
img_url

'https://assets.afcdn.com/recipe/20190220/88075__w1000h1000.jpg'